### Import libraries.

In [1]:
import pandas as pd
import numpy as np

import pickle
from functions import get_scores
from functions import run_model
from re import search
from tabulate import tabulate

from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import GridSearchCV, train_test_split, cross_val_score, StratifiedKFold
from sklearn.ensemble import RandomForestClassifier, ExtraTreesClassifier, GradientBoostingClassifier
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis
from sklearn.tree import DecisionTreeClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.ensemble import AdaBoostClassifier
from sklearn import svm
from sklearn import metrics

### Load data.

In [2]:
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
pd.set_option('display.max_colwidth', None)

In [3]:
# df = pickle.load(open("../datasets/occupancy.p", "rb"))
# df = pd.read_csv('../datasets/occupancy.csv')
df = pickle.load(open("../datasets/occupancy2.p", "rb"))

In [4]:
df

temperature   humidity       light          co2  \
date                                                                   
2015-02-04 17:51:00    23.180000  27.272000  426.000000   721.250000   
2015-02-04 17:52:00    23.150000  27.267500  429.500000   714.000000   
2015-02-04 17:53:00    23.150000  27.245000  426.000000   713.500000   
2015-02-04 17:54:00    23.150000  27.200000  426.000000   708.250000   
2015-02-04 17:55:00    23.100000  27.200000  426.000000   704.500000   
2015-02-04 17:56:00    23.100000  27.200000  419.000000   701.000000   
2015-02-04 17:57:00    23.100000  27.200000  419.000000   701.666667   
2015-02-04 17:58:00    23.100000  27.200000  419.000000   699.000000   
2015-02-04 17:59:00    23.100000  27.200000  419.000000   689.333333   
2015-02-04 18:00:00    23.075000  27.175000  419.000000   688.000000   
2015-02-04 18:01:00    23.075000  27.150000  419.000000   690.250000   
2015-02-04 18:02:00    23.100000  27.100000  419.000000   691.000000   
2015-02-04 18:03:00    23.100000  27.166667  419.000000   683.500000   
2015-02-04 18:04:00    23.050000  27.150000  419.000000   687.500000   
2015-02-04 18:05:00    23.000000  27.125000  419.000000   686.000000   
2015-02-04 18:06:00    23.000000  27.125000  418.500000   680.500000   
2015-02-04 18:07:00    23.000000  27.200000    0.000000   681.500000   
2015-02-04 18:08:00    22.945000  27.290000    0.000000   685.000000   
2015-02-04 18:09:00    22.945000  27.390000    0.000000   685.000000   
2015-02-04 18:10:00    22.890000  27.390000    0.000000   689.000000   
2015-02-04 18:11:00    22.890000  27.390000    0.000000   689.500000   
2015-02-04 18:12:00    22.890000  27.390000    0.000000   689.000000   
2015-02-04 18:13:00    22.890000  27.445000    0.000000   691.000000   
2015-02-04 18:14:00    22.890000  27.500000    0.000000   688.000000   
2015-02-04 18:15:00    22.890000  27.500000    0.000000   689.500000   
2015-02-04 18:16:00    22.790000  27.445000    0.000000   689.000000   
2015-02-04 18:17:00    22.790000  27.500000    0.000000   685.666667   
2015-02-04 18:18:00    22.790000  27.500000    0.000000   687.000000   
2015-02-04 18:19:00    22.790000  27.500000    0.000000   688.000000   
2015-02-04 18:20:00    22.745000  27.500000    0.000000   670.000000   
2015-02-04 18:21:00    22.700000  27.463333    0.000000   668.666667   
2015-02-04 18:22:00    22.700000  27.500000    0.000000   670.000000   
2015-02-04 18:23:00    22.700000  27.500000    0.000000   667.000000   
2015-02-04 18:24:00    22.666667  27.426667    0.000000   664.500000   
2015-02-04 18:25:00    22.700000  27.600000    0.000000   670.000000   
2015-02-04 18:26:00    22.600000  27.426667    0.000000   670.333333   
2015-02-04 18:27:00    22.600000  27.390000    0.000000   672.000000   
2015-02-04 18:28:00    22.600000  27.356667    0.000000   658.000000   
2015-02-04 18:29:00    22.600000  27.445000    0.000000   660.500000   
2015-02-04 18:30:00    22.600000  27.426667    0.000000   658.000000   
2015-02-04 18:31:00    22.600000  27.445000    0.000000   655.000000   
2015-02-04 18:32:00    22.600000  27.445000    0.000000   654.250000   
2015-02-04 18:33:00    22.600000  27.390000    0.000000   648.000000   
2015-02-04 18:34:00    22.500000  27.323333    0.000000   648.666667   
2015-02-04 18:35:00    22.500000  27.445000    0.000000   646.000000   
2015-02-04 18:36:00    22.500000  27.500000    0.000000   646.000000   
2015-02-04 18:37:00    22.500000  27.445000    0.000000   641.500000   
2015-02-04 18:38:00    22.390000  27.290000    0.000000   639.000000   
2015-02-04 18:39:00    22.500000  27.500000    0.000000   640.000000   
2015-02-04 18:40:00    22.390000  27.340000    0.000000   630.500000   
2015-02-04 18:41:00    22.390000  27.356667    0.000000   629.333333   
2015-02-04 18:42:00    22.390000  27.500000    0.000000   632.000000   
2015-02-04 18:43:00    22.390000  27.500000    0.000000   636.500000   
2015-02-04 18:44:00    22.390000  27.500000    0.000000   627

### Createa a dataframe for storing model scores

In [5]:
column_names = ['Model name', 'Features', 'Best score', 'Train score', 'Test score', 
                'Sensitivity', 'Specificity', 'Precision', 'Accuracy', 'F1-score']
scores_df = pd.DataFrame(columns=column_names)
scores_df.head()

Empty DataFrame
Columns: [Model name, Features, Best score, Train score, Test score, Sensitivity, Specificity, Precision, Accuracy, F1-score]
Index: []

### Features and target variables.

In [6]:
features_list = [['temperature', 'humidity', 'light', 'co2', 'humidity_ratio'],
                 ['temperature', 'humidity', 'light', 'co2'],
                 ['temperature', 'humidity', 'co2', 'humidity_ratio'],
                 ['temperature', 'humidity', 'light', 'humidity_ratio'],
                 ['temperature', 'humidity', 'humidity_ratio'],
                 ['temperature', 'humidity'],
                 ['temperature', 'light'],
                 ['humidity', 'light'],
                 ['light', 'humidity_ratio'],
                 ['temperature', 'co2'],
                 ['light', 'co2'],
                 ['temperature', 'humidity', 'light', 'co2', 'humidity_ratio', 'weekday'],
                 ['temperature', 'humidity', 'light', 'co2', 'weekday'],
                 ['temperature', 'humidity', 'co2', 'humidity_ratio', 'weekday'],
                 ['temperature', 'humidity', 'light', 'humidity_ratio', 'weekday'],
                 ['temperature', 'humidity', 'humidity_ratio', 'weekday'],
                 ['temperature', 'humidity', 'weekday'],
                 ['temperature', 'light', 'weekday'],
                 ['humidity', 'light', 'weekday'],
                 ['light', 'humidity_ratio', 'weekday'],
                 ['temperature', 'co2', 'weekday'],
                 ['light', 'co2', 'weekday']
                ]
target = 'occupancy'

### Initialize common grid search parameters for all models.

In [7]:
cv_folds = StratifiedKFold(n_splits=5, shuffle=True, random_state=0)
verbose = 1
n_jobs = 4

### Random Forest (RF)

In [8]:
model_name = 'rf'
params = { 
    'n_estimators' : [75,100,125],
    'max_features' : [None, 'auto'],
    'max_depth' : [None, 5, 6]
}

In [9]:
for i, features in enumerate(features_list):
    model = RandomForestClassifier(random_state=0)
    scores = run_model(df, features, target, params, model, model_name+str(i))
    scores_series = pd.Series(scores, index=scores_df.columns)
    scores_df = scores_df.append(scores_series, ignore_index=True)

Fitting 5 folds for each of 18 candidates, totalling 90 fits


[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  42 tasks      | elapsed:   10.5s
[Parallel(n_jobs=4)]: Done  90 out of  90 | elapsed:   18.2s finished


Fitting 5 folds for each of 18 candidates, totalling 90 fits


[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  42 tasks      | elapsed:    7.8s
[Parallel(n_jobs=4)]: Done  90 out of  90 | elapsed:   15.0s finished


Fitting 5 folds for each of 18 candidates, totalling 90 fits


...

[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  42 tasks      | elapsed:    4.9s
[Parallel(n_jobs=4)]: Done  90 out of  90 | elapsed:    9.7s finished


Fitting 5 folds for each of 18 candidates, totalling 90 fits


[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  42 tasks      | elapsed:    5.8s
[Parallel(n_jobs=4)]: Done  90 out of  90 | elapsed:   10.7s finished


Fitting 5 folds for each of 18 candidates, totalling 90 fits


[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  42 tasks      | elapsed:    4.8s
[Parallel(n_jobs=4)]: Done  90 out of  90 | elapsed:    9.3s finished


### Linear Discriminant Analysis (LDA)

In [10]:
# https://machinelearningmastery.com/linear-discriminant-analysis-with-python/

In [11]:
model_name = 'lda'
params = { 
    'solver' : ['svd', 'lsqr', 'eigen']
}

In [12]:
for i, features in enumerate(features_list):
    model = LinearDiscriminantAnalysis()
    scores = run_model(df, features, target, params, model, model_name+str(i))
    scores_series = pd.Series(scores, index=scores_df.columns)
    scores_df = scores_df.append(scores_series, ignore_index=True)

Fitting 5 folds for each of 3 candidates, totalling 15 fits
Fitting 5 folds for each of 3 candidates, totalling 15 fits


[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  15 out of  15 | elapsed:    0.1s finished
[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  15 out of  15 | elapsed:    0.1s finished
[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  15 out of  15 | elapsed:    0.1s finished
[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.


Fitting 5 folds for each of 3 candidates, totalling 15 fits
Fitting 5 folds for each of 3 candidates, totalling 15 fits


[Parallel(n_jobs=4)]: Done  15 out of  15 | elapsed:    0.1s finished
[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  15 out of  15 | elapsed:    0.1s finished
[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.


Fitting 5 folds for each of 3 candidates, totalling 15 fits
Fitting 5 folds for each of 3 candidates, totalling 15 fits


...

[Parallel(n_jobs=4)]: Done  15 out of  15 | elapsed:    0.1s finished
[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  15 out of  15 | elapsed:    0.1s finished
[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.


Fitting 5 folds for each of 3 candidates, totalling 15 fits
Fitting 5 folds for each of 3 candidates, totalling 15 fits


[Parallel(n_jobs=4)]: Done  15 out of  15 | elapsed:    0.1s finished
[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  15 out of  15 | elapsed:    0.1s finished
[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.


Fitting 5 folds for each of 3 candidates, totalling 15 fits
Fitting 5 folds for each of 3 candidates, totalling 15 fits


[Parallel(n_jobs=4)]: Done  15 out of  15 | elapsed:    0.1s finished


### Classification and Regression Trees (CART)

In [13]:
# https://www.datacamp.com/community/tutorials/decision-tree-classification-python

In [14]:
model_name = 'cart'
params = { 
    'max_depth' : [None, 2, 5],
    'max_features' : ['auto', 'sqrt', 'log2']
}

In [15]:
for i, features in enumerate(features_list):
    model = DecisionTreeClassifier(random_state=0)
    scores = run_model(df, features, target, params, model, model_name+str(i))
    scores_series = pd.Series(scores, index=scores_df.columns)
    scores_df = scores_df.append(scores_series, ignore_index=True)

[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.


Fitting 5 folds for each of 9 candidates, totalling 45 fits


[Parallel(n_jobs=4)]: Done  38 out of  45 | elapsed:    0.2s remaining:    0.0s
[Parallel(n_jobs=4)]: Done  45 out of  45 | elapsed:    0.2s finished
[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.


Fitting 5 folds for each of 9 candidates, totalling 45 fits


[Parallel(n_jobs=4)]: Done  45 out of  45 | elapsed:    0.2s finished
[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.


...

[Parallel(n_jobs=4)]: Done  45 out of  45 | elapsed:    0.1s finished
[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  38 out of  45 | elapsed:    0.1s remaining:    0.0s
[Parallel(n_jobs=4)]: Done  45 out of  45 | elapsed:    0.1s finished


Fitting 5 folds for each of 9 candidates, totalling 45 fits
Fitting 5 folds for each of 9 candidates, totalling 45 fits


[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  45 out of  45 | elapsed:    0.1s finished
[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.


Fitting 5 folds for each of 9 candidates, totalling 45 fits
Fitting 5 folds for each of 9 candidates, totalling 45 fits


[Parallel(n_jobs=4)]: Done  45 out of  45 | elapsed:    0.1s finished
[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  45 out of  45 | elapsed:    0.1s finished


### Gradient Boosting Machine (GBM)

In [16]:
# https://machinelearningmastery.com/gradient-boosting-machine-ensemble-in-python/

In [17]:
model_name = 'gbm'
params = { 
    'learning_rate' : [0.1, 0.2, 0.3],
    'n_estimators' : [100, 200],
    'max_depth' : [3, 5]
}

In [18]:
for i, features in enumerate(features_list):
    model = GradientBoostingClassifier(random_state=0)
    scores = run_model(df, features, target, params, model, model_name+str(i))
    scores_series = pd.Series(scores, index=scores_df.columns)
    scores_df = scores_df.append(scores_series, ignore_index=True)

Fitting 5 folds for each of 12 candidates, totalling 60 fits


[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  42 tasks      | elapsed:   16.2s
[Parallel(n_jobs=4)]: Done  60 out of  60 | elapsed:   24.9s finished


Fitting 5 folds for each of 12 candidates, totalling 60 fits


[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  42 tasks      | elapsed:   12.1s
[Parallel(n_jobs=4)]: Done  60 out of  60 | elapsed:   18.8s finished


Fitting 5 folds for each of 12 candidates, totalling 60 fits


...

[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  42 tasks      | elapsed:    8.3s
[Parallel(n_jobs=4)]: Done  60 out of  60 | elapsed:   13.0s finished


Fitting 5 folds for each of 12 candidates, totalling 60 fits


[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  42 tasks      | elapsed:    8.9s
[Parallel(n_jobs=4)]: Done  60 out of  60 | elapsed:   13.7s finished


Fitting 5 folds for each of 12 candidates, totalling 60 fits


[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  42 tasks      | elapsed:    7.7s
[Parallel(n_jobs=4)]: Done  60 out of  60 | elapsed:   23.5s finished


### K-Nearest Neighbor (KNN)

In [19]:
model_name = 'knn'
params = { 
    'n_neighbors' : [3, 5, 10],
    'p' : [1,2],
    'leaf_size' : [1, 5, 10]
}

In [20]:
for i, features in enumerate(features_list):
    model = KNeighborsClassifier()    
    scores = run_model(df, features, target, params, model, model_name+str(i))
    scores_series = pd.Series(scores, index=scores_df.columns)
    scores_df = scores_df.append(scores_series, ignore_index=True)

Fitting 5 folds for each of 18 candidates, totalling 90 fits


[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  76 tasks      | elapsed:    2.2s
[Parallel(n_jobs=4)]: Done  90 out of  90 | elapsed:    2.4s finished


Fitting 5 folds for each of 18 candidates, totalling 90 fits


[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  76 tasks      | elapsed:    1.7s
[Parallel(n_jobs=4)]: Done  90 out of  90 | elapsed:    2.0s finished


Fitting 5 folds for each of 18 candidates, totalling 90 fits


...

[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  76 tasks      | elapsed:    2.1s
[Parallel(n_jobs=4)]: Done  90 out of  90 | elapsed:    2.4s finished


Fitting 5 folds for each of 18 candidates, totalling 90 fits


[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  76 tasks      | elapsed:    1.6s
[Parallel(n_jobs=4)]: Done  90 out of  90 | elapsed:    1.8s finished


Fitting 5 folds for each of 18 candidates, totalling 90 fits


[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  76 tasks      | elapsed:    1.6s
[Parallel(n_jobs=4)]: Done  90 out of  90 | elapsed:    1.8s finished


### Support Vector Classification (SVC)

In [21]:
model_name = 'svc'
params = {
    'C': [0.1, 10, 100], 
    'gamma': [1,0.01,0.001],
    'kernel': ['rbf', 'sigmoid']
    }

In [22]:
for i, features in enumerate(features_list):
    model = svm.SVC()    
    scores = run_model(df, features, target, params, model, model_name+str(i))
    scores_series = pd.Series(scores, index=scores_df.columns)
    scores_df = scores_df.append(scores_series, ignore_index=True)

Fitting 5 folds for each of 18 candidates, totalling 90 fits


[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  42 tasks      | elapsed:   18.2s
[Parallel(n_jobs=4)]: Done  90 out of  90 | elapsed:   32.5s finished


Fitting 5 folds for each of 18 candidates, totalling 90 fits


[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  42 tasks      | elapsed:   15.5s
[Parallel(n_jobs=4)]: Done  90 out of  90 | elapsed:   28.9s finished


Fitting 5 folds for each of 18 candidates, totalling 90 fits


...

[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  42 tasks      | elapsed:    8.1s
[Parallel(n_jobs=4)]: Done  90 out of  90 | elapsed:   28.1s finished


Fitting 5 folds for each of 18 candidates, totalling 90 fits


[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  42 tasks      | elapsed:   16.3s
[Parallel(n_jobs=4)]: Done  90 out of  90 | elapsed:   37.3s finished


Fitting 5 folds for each of 18 candidates, totalling 90 fits


[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  42 tasks      | elapsed:   14.0s
[Parallel(n_jobs=4)]: Done  90 out of  90 | elapsed:   26.3s finished


### Adaptive Boosting (AdaBoost)

In [23]:
model_name = 'ada'
params = {
    'n_estimators' : [5, 10, 50],
    'learning_rate' : [1, 2]
    }

In [24]:
for i, features in enumerate(features_list):
    model = AdaBoostClassifier()    
    scores = run_model(df, features, target, params, model, model_name+str(i))
    scores_series = pd.Series(scores, index=scores_df.columns)
    scores_df = scores_df.append(scores_series, ignore_index=True)

Fitting 5 folds for each of 6 candidates, totalling 30 fits


[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  23 out of  30 | elapsed:    0.6s remaining:    0.2s
[Parallel(n_jobs=4)]: Done  30 out of  30 | elapsed:    1.1s finished
[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.


Fitting 5 folds for each of 6 candidates, totalling 30 fits


[Parallel(n_jobs=4)]: Done  23 out of  30 | elapsed:    0.5s remaining:    0.2s
[Parallel(n_jobs=4)]: Done  30 out of  30 | elapsed:    0.9s finished
[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.


Fitting 5 folds for each of 6 candidates, totalling 30 fits


...

[Parallel(n_jobs=4)]: Done  23 out of  30 | elapsed:    0.5s remaining:    0.1s
[Parallel(n_jobs=4)]: Done  30 out of  30 | elapsed:    0.7s finished
[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.


Fitting 5 folds for each of 6 candidates, totalling 30 fits


[Parallel(n_jobs=4)]: Done  23 out of  30 | elapsed:    0.5s remaining:    0.1s
[Parallel(n_jobs=4)]: Done  30 out of  30 | elapsed:    0.8s finished


Fitting 5 folds for each of 6 candidates, totalling 30 fits


[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  23 out of  30 | elapsed:    0.5s remaining:    0.2s
[Parallel(n_jobs=4)]: Done  30 out of  30 | elapsed:    0.8s finished


### Model summary table.

In [30]:
scores_df.head()

Model name                                           Features  Best score  \
0        rf0  temperature, humidity, light, co2, humidity_ratio      0.9937   
1        rf1                  temperature, humidity, light, co2      0.9940   
2        rf2         temperature, humidity, co2, humidity_ratio      0.9870   
3        rf3       temperature, humidity, light, humidity_ratio      0.9932   
4        rf4              temperature, humidity, humidity_ratio      0.9573   

   Train score  Test score  Sensitivity  Specificity  Precision  Accuracy  \
0       1.0000      0.9951       0.9884       0.9969     0.9884    0.9951   
1       1.0000      0.9955       0.9884       0.9974     0.9905    0.9955   
2       0.9999      0.9864       0.9672       0.9915     0.9682    0.9864   
3       0.9996      0.9951       0.9852       0.9977     0.9915    0.9951   
4       0.9905      0.9613       0.9037       0.9768     0.9124    0.9613   

   F1-score  
0    0.9884  
1    0.9894  
2    0.9677  
3    0.9883  
4    0.9080

In [26]:
"""
model_name = 'mnb'
scores_df = scores_df[~scores_df['Model name'].str.contains(model_name)]
scores_df.reset_index(drop=True, inplace=True)
""";

In [31]:
scores_df.sort_values(by='Accuracy', ascending=False).head(10)

Model name                                                    Features  \
12       rf12                  temperature, humidity, light, co2, weekday   
11       rf11  temperature, humidity, light, co2, humidity_ratio, weekday   
1         rf1                           temperature, humidity, light, co2   
14       rf14       temperature, humidity, light, humidity_ratio, weekday   
0         rf0           temperature, humidity, light, co2, humidity_ratio   
3         rf3                temperature, humidity, light, humidity_ratio   
78      gbm12                  temperature, humidity, light, co2, weekday   
18       rf18                                    humidity, light, weekday   
69       gbm3                temperature, humidity, light, humidity_ratio   
67       gbm1                           temperature, humidity, light, co2   

    Best score  Train score  Test score  Sensitivity  Specificity  Precision  \
12      0.9944       1.0000      0.9958       0.9905       0.9972     0.9894   
11      0.9943       1.0000      0.9955       0.9894       0.9972     0.9894   
1       0.9940       1.0000      0.9955       0.9884       0.9974     0.9905   
14      0.9940       0.9997      0.9953       0.9873       0.9974     0.9904   
0       0.9937       1.0000      0.9951       0.9884       0.9969     0.9884   
3       0.9932       0.9996      0.9951       0.9852       0.9977     0.9915   
78      0.9940       1.0000      0.9949       0.9862       0.9972     0.9894   
18      0.9920       0.9993      0.9944       0.9873       0.9963     0.9863   
69      0.9925       0.9996      0.9942       0.9831       0.9972     0.9894   
67      0.9929       1.0000      0.9942       0.9831       0.9972     0.9894   

    Accuracy  F1-score  
12    0.9958    0.9900  
11    0.9955    0.9894  
1     0.9955    0.9894  
14    0.9953    0.9889  
0     0.9951    0.9884  
3     0.9951    0.9883  
78    0.9949    0.9878  
18    0.9944    0.9868  
69    0.9942    0.9862  
67    0.9942    0.9862

In [32]:
scores_df.shape

(154, 10)

In [33]:
scores_df.to_csv('../models/scores3.csv', index=False)
scores_df.to_pickle('../models/scores3.p')

In [38]:
scores_df = pd.read_csv('../models/scores.csv')
scores_df.sort_values(by='Accuracy', ascending=False).head(10)

Model name                                           Features  Best score  \
1         rf1                  temperature, humidity, light, co2      0.9940   
0         rf0  temperature, humidity, light, co2, humidity_ratio      0.9938   
28       gbm1                  temperature, humidity, light, co2      0.9932   
27       gbm0  temperature, humidity, light, co2, humidity_ratio      0.9930   
3         rf3       temperature, humidity, light, humidity_ratio      0.9931   
30       gbm3       temperature, humidity, light, humidity_ratio      0.9925   
7         rf7                                    humidity, light      0.9911   
19      cart1                  temperature, humidity, light, co2      0.9925   
37       knn1                  temperature, humidity, light, co2      0.9908   
36       knn0  temperature, humidity, light, co2, humidity_ratio      0.9908   

    Train score  Test score  Sensitivity  Specificity  Precision  Accuracy  \
1        1.0000      0.9955       0.9884       0.9974     0.9905    0.9955   
0        1.0000      0.9953       0.9873       0.9974     0.9904    0.9953   
28       0.9989      0.9949       0.9873       0.9969     0.9883    0.9949   
27       1.0000      0.9944       0.9862       0.9966     0.9873    0.9944   
3        0.9996      0.9944       0.9831       0.9974     0.9904    0.9944   
30       0.9996      0.9940       0.9820       0.9972     0.9893    0.9940   
7        0.9994      0.9937       0.9831       0.9966     0.9872    0.9937   
19       1.0000      0.9931       0.9831       0.9957     0.9841    0.9931   
37       0.9945      0.9926       0.9894       0.9935     0.9760    0.9926   
36       0.9945      0.9926       0.9894       0.9935     0.9760    0.9926   

    F1-score  
1     0.9894  
0     0.9889  
28    0.9878  
27    0.9868  
3     0.9867  
30    0.9857  
7     0.9852  
19    0.9836  
37    0.9827  
36    0.9827

In [36]:
scores2_df = pd.read_csv('../models/scores2.csv')
scores2_df.sort_values(by='Accuracy', ascending=False).head(10)

Model name                                                    Features  \
14       rf14       temperature, humidity, light, humidity_ratio, weekday   
12       rf12                  temperature, humidity, light, co2, weekday   
11       rf11  temperature, humidity, light, co2, humidity_ratio, weekday   
1         rf1                           temperature, humidity, light, co2   
0         rf0           temperature, humidity, light, co2, humidity_ratio   
77      gbm11  temperature, humidity, light, co2, humidity_ratio, weekday   
67       gbm1                           temperature, humidity, light, co2   
18       rf18                                    humidity, light, weekday   
3         rf3                temperature, humidity, light, humidity_ratio   
66       gbm0           temperature, humidity, light, co2, humidity_ratio   

    Best score  Train score  Test score  Sensitivity  Specificity  Precision  \
14      0.9940       0.9996      0.9960       0.9905       0.9974     0.9905   
12      0.9945       1.0000      0.9958       0.9894       0.9974     0.9905   
11      0.9946       1.0000      0.9955       0.9905       0.9969     0.9884   
1       0.9940       1.0000      0.9955       0.9884       0.9974     0.9905   
0       0.9938       1.0000      0.9953       0.9873       0.9974     0.9904   
77      0.9940       1.0000      0.9951       0.9884       0.9969     0.9884   
67      0.9932       0.9989      0.9949       0.9873       0.9969     0.9883   
18      0.9920       0.9994      0.9949       0.9884       0.9966     0.9873   
3       0.9931       0.9996      0.9944       0.9831       0.9974     0.9904   
66      0.9930       1.0000      0.9944       0.9862       0.9966     0.9873   

    Accuracy  F1-score  
14    0.9960    0.9905  
12    0.9958    0.9899  
11    0.9955    0.9894  
1     0.9955    0.9894  
0     0.9953    0.9889  
77    0.9951    0.9884  
67    0.9949    0.9878  
18    0.9949    0.9878  
3     0.9944    0.9867  
66    0.9944    0.9868

In [34]:
scores3_df = pd.read_csv('../models/scores3.csv')
scores3_df.sort_values(by='Accuracy', ascending=False).head(10)

Model name                                                    Features  \
12       rf12                  temperature, humidity, light, co2, weekday   
11       rf11  temperature, humidity, light, co2, humidity_ratio, weekday   
1         rf1                           temperature, humidity, light, co2   
14       rf14       temperature, humidity, light, humidity_ratio, weekday   
0         rf0           temperature, humidity, light, co2, humidity_ratio   
3         rf3                temperature, humidity, light, humidity_ratio   
78      gbm12                  temperature, humidity, light, co2, weekday   
18       rf18                                    humidity, light, weekday   
69       gbm3                temperature, humidity, light, humidity_ratio   
67       gbm1                           temperature, humidity, light, co2   

    Best score  Train score  Test score  Sensitivity  Specificity  Precision  \
12      0.9944       1.0000      0.9958       0.9905       0.9972     0.9894   
11      0.9943       1.0000      0.9955       0.9894       0.9972     0.9894   
1       0.9940       1.0000      0.9955       0.9884       0.9974     0.9905   
14      0.9940       0.9997      0.9953       0.9873       0.9974     0.9904   
0       0.9937       1.0000      0.9951       0.9884       0.9969     0.9884   
3       0.9932       0.9996      0.9951       0.9852       0.9977     0.9915   
78      0.9940       1.0000      0.9949       0.9862       0.9972     0.9894   
18      0.9920       0.9993      0.9944       0.9873       0.9963     0.9863   
69      0.9925       0.9996      0.9942       0.9831       0.9972     0.9894   
67      0.9929       1.0000      0.9942       0.9831       0.9972     0.9894   

    Accuracy  F1-score  
12    0.9958    0.9900  
11    0.9955    0.9894  
1     0.9955    0.9894  
14    0.9953    0.9889  
0     0.9951    0.9884  
3     0.9951    0.9883  
78    0.9949    0.9878  
18    0.9944    0.9868  
69    0.9942    0.9862  
67    0.9942    0.9862

In [39]:
scores_df.shape, scores2_df.shape, scores3_df.shape

((63, 10), (154, 10), (154, 10))

In [12]:
print(tabulate(scores2_df.sort_values(by='Accuracy', ascending=False).head(10), tablefmt="pipe", headers="keys"))

|    | Model name   | Features                                                   |   Best score |   Train score |   Test score |   Sensitivity |   Specificity |   Precision |   Accuracy |   F1-score |
|---:|:-------------|:-----------------------------------------------------------|-------------:|--------------:|-------------:|--------------:|--------------:|------------:|-----------:|-----------:|
| 14 | rf14         | temperature, humidity, light, humidity_ratio, weekday      |       0.994  |        0.9996 |       0.996  |        0.9905 |        0.9974 |      0.9905 |     0.996  |     0.9905 |
| 12 | rf12         | temperature, humidity, light, co2, weekday                 |       0.9945 |        1      |       0.9958 |        0.9894 |        0.9974 |      0.9905 |     0.9958 |     0.9899 |
| 11 | rf11         | temperature, humidity, light, co2, humidity_ratio, weekday |       0.9946 |        1      |       0.9955 |        0.9905 |        0.9969 |      0.9884 |     0.9955 |     0.98